In [46]:
sentence = ("In this movie, Truman is a man whose life is a fake one... The place he lives is in fact a big studio with hidden cameras everywhere, and all his friends and people around him, are actors who play their roles in the most popular TV-series in the world: The Truman Show. Truman thinks that he is an ordinary man with an ordinary life and has no idea about how he is exploited. Until one day... he finds out everything. Will he react?")

In [45]:
tf.reset_default_graph()

In [47]:
import tensorflow as tf
import numpy as np
from tensorflow.contrib import rnn
tf.set_random_seed(777)

In [48]:
char_set = list(set(sentence))
char_set

['k',
 'n',
 'V',
 'h',
 'T',
 ' ',
 'W',
 'd',
 's',
 '-',
 'x',
 'b',
 'y',
 '.',
 'u',
 ':',
 'o',
 'e',
 '?',
 ',',
 'a',
 'f',
 'c',
 'U',
 'g',
 'p',
 't',
 'i',
 'v',
 'w',
 'l',
 'm',
 'S',
 'r',
 'I']

In [49]:
char_dic = {w : i for i,w in enumerate(char_set)}
char_dic

{' ': 5,
 ',': 19,
 '-': 9,
 '.': 13,
 ':': 15,
 '?': 18,
 'I': 34,
 'S': 32,
 'T': 4,
 'U': 23,
 'V': 2,
 'W': 6,
 'a': 20,
 'b': 11,
 'c': 22,
 'd': 7,
 'e': 17,
 'f': 21,
 'g': 24,
 'h': 3,
 'i': 27,
 'k': 0,
 'l': 30,
 'm': 31,
 'n': 1,
 'o': 16,
 'p': 25,
 'r': 33,
 's': 8,
 't': 26,
 'u': 14,
 'v': 28,
 'w': 29,
 'x': 10,
 'y': 12}

In [50]:
dataX=[]
dataY=[]
seq_length = 7

In [51]:
for i in range(0,len(sentence) - seq_length):
    x_str = sentence[i:i+seq_length]
    y_str = sentence[i+1:i+1+seq_length]
    print(i,x_str,'->',y_str)
    
    x = [char_dic[c] for c in x_str]
    y = [char_dic[c] for c in y_str]
    
    dataX.append(x)
    dataY.append(y)

0 In this -> n this 
1 n this  ->  this m
2  this m -> this mo
3 this mo -> his mov
4 his mov -> is movi
5 is movi -> s movie
6 s movie ->  movie,
7  movie, -> movie, 
8 movie,  -> ovie, T
9 ovie, T -> vie, Tr
10 vie, Tr -> ie, Tru
11 ie, Tru -> e, Trum
12 e, Trum -> , Truma
13 , Truma ->  Truman
14  Truman -> Truman 
15 Truman  -> ruman i
16 ruman i -> uman is
17 uman is -> man is 
18 man is  -> an is a
19 an is a -> n is a 
20 n is a  ->  is a m
21  is a m -> is a ma
22 is a ma -> s a man
23 s a man ->  a man 
24  a man  -> a man w
25 a man w ->  man wh
26  man wh -> man who
27 man who -> an whos
28 an whos -> n whose
29 n whose ->  whose 
30  whose  -> whose l
31 whose l -> hose li
32 hose li -> ose lif
33 ose lif -> se life
34 se life -> e life 
35 e life  ->  life i
36  life i -> life is
37 life is -> ife is 
38 ife is  -> fe is a
39 fe is a -> e is a 
40 e is a  ->  is a f
41  is a f -> is a fa
42 is a fa -> s a fak
43 s a fak ->  a fake
44  a fake -> a fake 
45 a fake  ->  fake 

417  Will h -> Will he
418 Will he -> ill he 
419 ill he  -> ll he r
420 ll he r -> l he re
421 l he re ->  he rea
422  he rea -> he reac
423 he reac -> e react
424 e react ->  react?


In [52]:
data_dim = len(char_set)
hidden_size = len(char_set)
num_classes = len(char_set)
batch_size = len(dataX)

In [53]:
X = tf.placeholder(tf.int32,[None,seq_length])
Y = tf.placeholder(tf.int32,[None,seq_length])
X_one_hot = tf.one_hot(X,num_classes)
print(X_one_hot)

Tensor("one_hot:0", shape=(?, 7, 35), dtype=float32)


In [20]:
def lstm_cell():
    cell = tf.nn.rnn_cell.BasicLSTMCell(num_units=hidden_size,
                                       state_is_tuple=True)
    return cell

In [21]:
multi_cells = rnn.MultiRNNCell([lstm_cell() for _ in range(2)],state_is_tuple=True)


Instructions for updating:
This class is deprecated, please use tf.nn.rnn_cell.LSTMCell, which supports all the feature this cell currently has. Please replace the existing code with tf.nn.rnn_cell.LSTMCell(name='basic_lstm_cell').


In [23]:
outputs,states = tf.nn.dynamic_rnn(multi_cells,X_one_hot,dtype=tf.float32)

In [24]:
X_for_fc = tf.reshape(outputs,[-1,hidden_size])
outputs = tf.contrib.layers.fully_connected(X_for_fc,num_classes,activation_fn=None)


In [56]:
#outputs = tf.reshape(outputs,[batch_size,seq_length,num_classes])
weights = tf.ones([batch_size,seq_length])


In [57]:
sequence_loss = tf.contrib.seq2seq.sequence_loss(logits=outputs2,targets=Y,weights=weights)
loss = tf.reduce_mean(sequence_loss)
train = tf.train.AdamOptimizer(learning_rate=0.1).minimize(loss)

In [58]:
sess = tf.Session()
sess.run(tf.global_variables_initializer())

In [60]:
for i in range(500):
    _,l,results = sess.run([train,loss,outputs2],feed_dict={X:dataX,Y:dataY})
    
    for j,result in enumerate(results):
        index = np.argmax(result, axis=1)
        print(i,j,''.join([char_set[t] for t in index]), l)

0 0 iiiiiii 3.619665
0 1 ii,,,ii 3.619665
0 2 iiiiiii 3.619665
0 3 iiiiiii 3.619665
0 4 iiiiiii 3.619665
0 5 iiiiiii 3.619665
0 6 iiiiiii 3.619665
0 7 ii,,,,, 3.619665
0 8 ii,,i,, 3.619665
0 9 iiiiiii 3.619665
0 10 iiiiiii 3.619665
0 11 iiiiii, 3.619665
0 12 iiii,,, 3.619665
0 13 iii,,,, 3.619665
0 14 iii,,,, 3.619665
0 15 iii,i,, 3.619665
0 16 ii,i,,, 3.619665
0 17 iii,,,, 3.619665
0 18 iiiiiii 3.619665
0 19 iiiiiii 3.619665
0 20 iiiiiii 3.619665
0 21 iiiiiii 3.619665
0 22 iiiiiii 3.619665
0 23 iiiiiii 3.619665
0 24 iiiii,, 3.619665
0 25 iiiiii, 3.619665
0 26 iii,,,, 3.619665
0 27 iiii,,, 3.619665
0 28 iiiiiii 3.619665
0 29 ii,,,ii 3.619665
0 30 iii,iii 3.619665
0 31 iiiiiii 3.619665
0 32 iiiiiii 3.619665
0 33 iiiiiii 3.619665
0 34 iiiiiii 3.619665
0 35 iiiiiii 3.619665
0 36 iiiiii, 3.619665
0 37 iiiiiii 3.619665
0 38 iiiiiii 3.619665
0 39 iiiiiii 3.619665
0 40 iiiiiii 3.619665
0 41 iiiiiii 3.619665
0 42 iiiiiii 3.619665
0 43 iiiiiii 3.619665
0 44 iiiiiii 3.619665
0 45 iiiiiii 3.61966

1 178 iiiiiii 3.4853413
1 179 iiiiiii 3.4853413
1 180 iiiiiii 3.4853413
1 181 iiiiiii 3.4853413
1 182 iiiiiii 3.4853413
1 183 iiiiiii 3.4853413
1 184 iiiiiii 3.4853413
1 185 iiiiiii 3.4853413
1 186 iiiiiii 3.4853413
1 187 iiiiiii 3.4853413
1 188 iiiiiii 3.4853413
1 189 iiiiii  3.4853413
1 190 iiiii f 3.4853413
1 191 iiii  f 3.4853413
1 192 iiii    3.4853413
1 193 iiiii   3.4853413
1 194 iiiii   3.4853413
1 195 iiiiiii 3.4853413
1 196 iiiiiii 3.4853413
1 197 iiiiiii 3.4853413
1 198 iiiiiii 3.4853413
1 199 iiiiiii 3.4853413
1 200 iiiiiii 3.4853413
1 201 iiiiiii 3.4853413
1 202 iiiiiii 3.4853413
1 203 iiiiiii 3.4853413
1 204 iiiiii  3.4853413
1 205 iiiii   3.4853413
1 206 iiiiiii 3.4853413
1 207 iiiiii  3.4853413
1 208 iiiiiii 3.4853413
1 209 iiiiiii 3.4853413
1 210 iiiiiii 3.4853413
1 211 iiiiiii 3.4853413
1 212 iiiiiii 3.4853413
1 213 iiiiiii 3.4853413
1 214 iiiiiii 3.4853413
1 215 iiiiiii 3.4853413
1 216 iiiii i 3.4853413
1 217 iiiiiii 3.4853413
1 218 iiiiiii 3.4853413
1 219 iiiiii  3.

2 253 ii      3.1632202
2 254 ii      3.1632202
2 255 ii      3.1632202
2 256 ii      3.1632202
2 257 ii      3.1632202
2 258 ii      3.1632202
2 259 ii      3.1632202
2 260 ii      3.1632202
2 261 i       3.1632202
2 262 ii      3.1632202
2 263 ii      3.1632202
2 264 ii      3.1632202
2 265 ii      3.1632202
2 266 ii      3.1632202
2 267 ii      3.1632202
2 268 ii      3.1632202
2 269 ii      3.1632202
2 270 ii      3.1632202
2 271 ii      3.1632202
2 272 ii      3.1632202
2 273 ii      3.1632202
2 274 i       3.1632202
2 275 ii      3.1632202
2 276 ii      3.1632202
2 277 ii      3.1632202
2 278 i       3.1632202
2 279 ii      3.1632202
2 280 ii      3.1632202
2 281 ii      3.1632202
2 282 ii      3.1632202
2 283 ii      3.1632202
2 284 ii      3.1632202
2 285 i       3.1632202
2 286 i       3.1632202
2 287 ii      3.1632202
2 288 ii      3.1632202
2 289 ii      3.1632202
2 290 ii      3.1632202
2 291 ii      3.1632202
2 292 i       3.1632202
2 293 ii      3.1632202
2 294 ii      3.

3 327 e       2.9994762
3 328         2.9994762
3 329         2.9994762
3 330         2.9994762
3 331         2.9994762
3 332 e       2.9994762
3 333         2.9994762
3 334         2.9994762
3 335         2.9994762
3 336 e       2.9994762
3 337         2.9994762
3 338         2.9994762
3 339         2.9994762
3 340 e       2.9994762
3 341         2.9994762
3 342 i       2.9994762
3 343 e       2.9994762
3 344         2.9994762
3 345         2.9994762
3 346         2.9994762
3 347         2.9994762
3 348 e       2.9994762
3 349         2.9994762
3 350         2.9994762
3 351 i       2.9994762
3 352         2.9994762
3 353         2.9994762
3 354 e       2.9994762
3 355         2.9994762
3 356 i       2.9994762
3 357 i       2.9994762
3 358 e       2.9994762
3 359         2.9994762
3 360         2.9994762
3 361 e       2.9994762
3 362         2.9994762
3 363         2.9994762
3 364 e       2.9994762
3 365         2.9994762
3 366 i       2.9994762
3 367 e       2.9994762
3 368         2.

4 402         2.9627025
4 403         2.9627025
4 404         2.9627025
4 405         2.9627025
4 406         2.9627025
4 407         2.9627025
4 408         2.9627025
4 409         2.9627025
4 410         2.9627025
4 411         2.9627025
4 412         2.9627025
4 413         2.9627025
4 414         2.9627025
4 415         2.9627025
4 416         2.9627025
4 417         2.9627025
4 418         2.9627025
4 419         2.9627025
4 420         2.9627025
4 421         2.9627025
4 422         2.9627025
4 423         2.9627025
4 424         2.9627025
5 0         2.949692
5 1         2.949692
5 2         2.949692
5 3         2.949692
5 4         2.949692
5 5         2.949692
5 6         2.949692
5 7         2.949692
5 8         2.949692
5 9         2.949692
5 10         2.949692
5 11         2.949692
5 12         2.949692
5 13         2.949692
5 14         2.949692
5 15         2.949692
5 16         2.949692
5 17         2.949692
5 18         2.949692
5 19         2.949692
5 20         2.949

...

494 297 ardinar 0.44370583
494 298 rdinary 0.44370583
494 299 yinary  0.44370583
494 300  nary l 0.44370583
494 301 nary la 0.44370583
494 302  ry lan 0.44370583
494 303 ny lan  0.44370583
494 304 y man w 0.44370583
494 305  lan wi 0.44370583
494 306 aan wht 0.44370583
494 307 an whth 0.44370583
494 308 n whth  0.44370583
494 309  thth a 0.44370583
494 310 ahth an 0.44370583
494 311 hth an  0.44370583
494 312 nh an o 0.44370583
494 313 hian or 0.44370583
494 314 ean ord 0.44370583
494 315 andordi 0.44370583
494 316 n wrdin 0.44370583
494 317  trdina 0.44370583
494 318 ardinar 0.44370583
494 319 rdinary 0.44370583
494 320 yinary  0.44370583
494 321  nary l 0.44370583
494 322 nary li 0.44370583
494 323  ry lif 0.44370583
494 324 ny life 0.44370583
494 325 y mife  0.44370583
494 326  life a 0.44370583
494 327 aife an 0.44370583
494 328 afe and 0.44370583
494 329 ne and  0.44370583
494 330 a and h 0.44370583
494 331  ard ha 0.44370583
494 332 and pas 0.44370583
494 333 n  aas  0.44370583
4

495 372  . Unti 0.44341063
495 373   Until 0.44341063
495 374  Tntil  0.44341063
495 375 antil o 0.44341063
495 376 ntil on 0.44341063
495 377  il one 0.44341063
495 378 hl one  0.44341063
495 379 n one d 0.44341063
495 380  hne da 0.44341063
495 381 ane day 0.44341063
495 382  e day. 0.44341063
495 383   day.. 0.44341063
495 384  iay... 0.44341063
495 385 aay...  0.44341063
495 386  y... h 0.44341063
495 387 n .. he 0.44341063
495 388  .. he  0.44341063
495 389    he f 0.44341063
495 390   he fi 0.44341063
495 391  Te fin 0.44341063
495 392 ae iind 0.44341063
495 393 e iinds 0.44341063
495 394  iinds  0.44341063
495 395 aands o 0.44341063
495 396 ends ou 0.44341063
495 397 n s out 0.44341063
495 398    out  0.44341063
495 399   out e 0.44341063
495 400  iut ev 0.44341063
495 401 ant eve 0.44341063
495 402  t ever 0.44341063
495 403 m hvery 0.44341063
495 404 hhveryt 0.44341063
495 405 averywh 0.44341063
495 406  erywhi 0.44341063
495 407 erywhin 0.44341063
495 408  ything 0.44341063
4

497 22 n a fan 0.4430087
497 23  anman  0.4430087
497 24 anman w 0.4430087
497 25 nman wh 0.4430087
497 26 aon wio 0.4430087
497 27 an whos 0.4430087
497 28 n ohose 0.4430087
497 29  tiose  0.4430087
497 30 aio e l 0.4430087
497 31 ho e li 0.4430087
497 32 ewe lif 0.4430087
497 33 re life 0.4430087
497 34   life  0.4430087
497 35  aife i 0.4430087
497 36 aife as 0.4430087
497 37  fe as  0.4430087
497 38 ne as a 0.4430087
497 39 e as a  0.4430087
497 40  as anf 0.4430087
497 41 as a fa 0.4430087
497 42 n a fak 0.4430087
497 43  anmake 0.4430087
497 44 anmake  0.4430087
497 45 nmake o 0.4430087
497 46 aake on 0.4430087
497 47 eke one 0.4430087
497 48 ne one. 0.4430087
497 49 e one.. 0.4430087
497 50  ane... 0.4430087
497 51 ane ..  0.4430087
497 52 re .. T 0.4430087
497 53   .. Th 0.4430087
497 54  .. The 0.4430087
497 55    The  0.4430087
497 56   The p 0.4430087
497 57  The pl 0.4430087
497 58 are pla 0.4430087
497 59 re plac 0.4430087
497 60 e ilace 0.4430087
497 61  alace  0.4430087


498 97 mio wit 0.44356275
498 98  n with 0.44356275
498 99 n with  0.44356275
498 100 rwith h 0.44356275
498 101 ahth hi 0.44356275
498 102 hth hid 0.44356275
498 103 nh hidd 0.44356275
498 104 hihidde 0.44356275
498 105 ehidden 0.44356275
498 106 aesden  0.44356275
498 107 esden c 0.44356275
498 108 nden ca 0.44356275
498 109  en cam 0.44356275
498 110  n came 0.44356275
498 111  dcamer 0.44356275
498 112  tamera 0.44356275
498 113 aameras 0.44356275
498 114 tmeras  0.44356275
498 115 neras e 0.44356275
498 116 aras ev 0.44356275
498 117  ys eve 0.44356275
498 118 ys ever 0.44356275
498 119 n nvery 0.44356275
498 120  ixeryw 0.44356275
498 121 averywh 0.44356275
498 122  erywhe 0.44356275
498 123 erywher 0.44356275
498 124  ywhere 0.44356275
498 125 y here, 0.44356275
498 126  here,  0.44356275
498 127 hore, a 0.44356275
498 128 e e, an 0.44356275
498 129  y, and 0.44356275
498 130 y, and  0.44356275
498 131   Tnd a 0.44356275
498 132  ard al 0.44356275
498 133 and hll 0.44356275
498 

499 171 aem, ar 0.44375026
499 172 en, are 0.44375026
499 173 n, are  0.44375026
499 174 a are a 0.44375026
499 175  are ac 0.44375026
499 176 ane act 0.44375026
499 177 ny acto 0.44375026
499 178 y actor 0.44375026
499 179  artors 0.44375026
499 180 antors  0.44375026
499 181 nt rs w 0.44375026
499 182 t rs wh 0.44375026
499 183 hrs who 0.44375026
499 184 rd who  0.44375026
499 185 y who p 0.44375026
499 186  aho pl 0.44375026
499 187 aho pla 0.44375026
499 188 ho play 0.44375026
499 189 ewplay  0.44375026
499 190 rilay t 0.44375026
499 191 alay th 0.44375026
499 192 lay the 0.44375026
499 193 ay thei 0.44375026
499 194 n their 0.44375026
499 195  lheir  0.44375026
499 196 ahe r r 0.44375026
499 197 he r ro 0.44375026
499 198 e r rol 0.44375026
499 199  r role 0.44375026
499 200 n roles 0.44375026
499 201 yToles  0.44375026
499 202 aoles i 0.44375026
499 203 yues in 0.44375026
499 204 res in  0.44375026
499 205 a  in t 0.44375026
499 206   in th 0.44375026
499 207  an the 0.44375026
4

In [62]:
results = sess.run(outputs,feed_dict={X:dataX})
for j, result in enumerate(results):
    index = np.argmax(result,axis=1)
    if j is 0:
        print(''.join([char_set[t] for t in index]), end='')
    else:
        print(char_set[index[-1]],end='')

ValueError: Fetch argument <tf.Tensor 'Reshape_1:0' shape=(425, 7, 35) dtype=float32> cannot be interpreted as a Tensor. (Tensor Tensor("Reshape_1:0", shape=(425, 7, 35), dtype=float32) is not an element of this graph.)

In [54]:
cell2 = tf.nn.rnn_cell.BasicLSTMCell(hidden_size,state_is_tuple=True)
cell2 = rnn.MultiRNNCell([cell2]*2,state_is_tuple=True)
outputs2,states2 = tf.nn.dynamic_rnn(cell2,X_one_hot,dtype=tf.float32)

In [55]:
x_for_soft = tf.reshape(outputs2,[-1,hidden_size])
soft_W = tf.get_variable("soft_W",[hidden_size,num_classes])
soft_b = tf.get_variable("soft_b",[num_classes])
outputs2 = tf.matmul(x_for_soft,soft_W) + soft_b

outputs2 = tf.reshape(outputs2,[batch_size,seq_length,num_classes])